In [19]:
import requests
from bs4 import BeautifulSoup
import time
import sqlite3
import os

DB_NAME = "suumo_listings.db"  # DBファイル名

def init_db():
    """
    SQLiteデータベース(ファイル)を開き、テーブル`listings`が存在しなければ作成する。
    """
    conn = sqlite3.connect(DB_NAME)
    cursor = conn.cursor()
    
    # テーブルが存在しなければ作成
    create_table_query = """
    CREATE TABLE IF NOT EXISTS listings (
        id INTEGER PRIMARY KEY AUTOINCREMENT,
        title TEXT,
        bus_walk TEXT,
        price TEXT,
        management_fee TEXT,
        reikin_shikikin TEXT,
        area TEXT,
        layout TEXT,
        age TEXT
    )
    """
    cursor.execute(create_table_query)
    
    # 変更を確定
    conn.commit()
    conn.close()

def insert_listing_to_db(house_data):
    """
    1件の物件情報(house_data)をSQLiteのlistingsテーブルに挿入する。
    """
    conn = sqlite3.connect(DB_NAME)
    cursor = conn.cursor()
    
    insert_query = """
    INSERT INTO listings 
    (title, bus_walk, price, management_fee, reikin_shikikin, area, layout, age)
    VALUES (?, ?, ?, ?, ?, ?, ?, ?)
    """
    cursor.execute(insert_query, (
        house_data.get('title'), 
        house_data.get('bus_walk'), 
        house_data.get('price'), 
        house_data.get('management_fee'),
        house_data.get('reikin_shikikin'),
        house_data.get('area'),
        house_data.get('layout'),
        house_data.get('age')
    ))
    
    conn.commit()
    conn.close()

def scrape_suumo_page(page_num):
    """
    指定したページ番号(page_num)でのSUUMO賃貸情報をスクレイピングし、
    取得した物件情報をリストとして返す。
    """
    base_url = "https://suumo.jp/jj/common/ichiran/JJ901FC004/"
    # 主要パラメータ
    params = {
        "pc": "30",
        "seniFlg": "1",
        "ar": "030",
        "ra": "030013",
        "rn": "0090",
        "rnek": ["009014660","009025630","009025440","009053940","009005480"],  
        "rnTmp": "0090",
        "kwd": "",
        "bs": "040",
        "cb": "0.0",
        "ct": "9999999",
        "kb": "0",
        "kt": "9999999",
        "km": "1",
        "xb": "0",
        "xt": "9999999",
        "et": "9999999",
        "cn": "9999999",
        "newflg": "0",
        "pn": str(page_num)  # ページ番号
    }

    response = requests.get(base_url, params=params)
    if response.status_code == 200:
        soup = BeautifulSoup(response.text, 'html.parser')
        
        houses_on_page = []
        listings = soup.find_all('div', class_='cassettebox js-normalLink js-cassetLink')

        for listing in listings:
            house_data = {}
            
            # ========= 1. 物件タイトル取得 =========
            title_elem = listing.find('h2', class_='cassettebox-title')
            if title_elem:
                link_tag = title_elem.find('a')
                house_data['title'] = link_tag.get_text(strip=True) if link_tag else title_elem.get_text(strip=True)
            else:
                house_data['title'] = "タイトルなし"

            # ========= 2. テーブルを取得 =========
            tables = listing.find_all('table', class_='listtable')
            
            # (A) 1つ目のtable → バス/徒歩
            first_table = tables[0] if len(tables) > 0 else None
            if first_table:
                row_data = first_table.find_all('tr')
                if len(row_data) > 1:
                    col_data = row_data[1].find_all('td')
                    if len(col_data) >= 3:
                        bus_walk_text = col_data[2].get_text(separator='', strip=True)
                        house_data['bus_walk'] = bus_walk_text
                    else:
                        house_data['bus_walk'] = "バス/徒歩情報なし"
                else:
                    house_data['bus_walk'] = "バス/徒歩情報なし"
            else:
                house_data['bus_walk'] = "バス/徒歩情報なし"

            # (B) 2つ目のtable → 賃料,管理費,礼金/敷金,面積,間取り,築年数
            second_table = tables[1] if len(tables) > 1 else None
            if second_table:
                row_data = second_table.find_all('tr')
                if len(row_data) > 1:
                    cols = row_data[1].find_all('td')
                    
                    # (1) price, management_fee, reikin_shikikin
                    if len(cols) > 0:
                        first_td = cols[0]
                        if first_td:
                            dl_list = first_td.find_all('dl', class_='infodatabox-details')
                            for dl in dl_list:
                                dt = dl.find('dt', class_='infodatabox-details-title')
                                dd = dl.find('dd', class_='infodatabox-details-txt')
                                if dt and dd:
                                    dt_text = dt.get_text(strip=True)
                                    dd_text = dd.get_text(strip=True)
                                    if "賃料" in dt_text:
                                        house_data['price'] = dd_text
                                    elif "管理・共益費" in dt_text:
                                        house_data['management_fee'] = dd_text
                                    elif "礼金/敷金" in dt_text:
                                        house_data['reikin_shikikin'] = dd_text

                    # (2) area, layout
                    if len(cols) > 1:
                        second_td = cols[1]
                        if second_td:
                            dl_list = second_td.find_all('dl', class_='infodatabox-details')
                            for dl in dl_list:
                                dt = dl.find('dt', class_='infodatabox-details-title')
                                dd = dl.find('dd', class_='infodatabox-details-txt')
                                if dt and dd:
                                    dt_text = dt.get_text(strip=True)
                                    dd_text = dd.get_text(separator='', strip=True)
                                    if "専有面積" in dt_text:
                                        house_data['area'] = dd_text
                                    elif "間取り" in dt_text:
                                        house_data['layout'] = dd_text

                    # (3) 築年数
                    if len(cols) > 2:
                        third_td = cols[2]
                        if third_td:
                            house_data['age'] = third_td.get_text(strip=True)
                        else:
                            house_data['age'] = "築年数情報なし"
                    else:
                        house_data['age'] = "築年数情報なし"
                else:
                    house_data['price'] = "賃料情報なし"
                    house_data['management_fee'] = "管理費情報なし"
                    house_data['reikin_shikikin'] = "礼金/敷金情報なし"
                    house_data['area'] = "面積情報なし"
                    house_data['layout'] = "間取り情報なし"
                    house_data['age'] = "築年数情報なし"
            else:
                house_data['price'] = "賃料情報なし"
                house_data['management_fee'] = "管理費情報なし"
                house_data['reikin_shikikin'] = "礼金/敷金情報なし"
                house_data['area'] = "面積情報なし"
                house_data['layout'] = "間取り情報なし"
                house_data['age'] = "築年数情報なし"
            
            houses_on_page.append(house_data)
        
        return houses_on_page
    else:
        print(f"Error: HTTP status code {response.status_code} at page {page_num}")
        return []

def main():
    # まずDB初期化（テーブルなければ作成）
    init_db()

    # すべてのページ(例: 1～577ページ)をスクレイピング
    max_page = 577
    for page in range(1, max_page+1):
        print(f"Scraping page {page} ...")
        houses_on_current_page = scrape_suumo_page(page)
        
        # 取得した各物件をDBにINSERT
        for house_data in houses_on_current_page:
            insert_listing_to_db(house_data)
        
        # 大量アクセスを防ぐためのスリープ
        time.sleep(1)
    
    print("スクレイピング完了。DBに保存しました。")

if __name__ == "__main__":
    main()

Scraping page 1 ...
Scraping page 2 ...
Scraping page 3 ...
Scraping page 4 ...
Scraping page 5 ...
Scraping page 6 ...
Scraping page 7 ...
Scraping page 8 ...
Scraping page 9 ...
Scraping page 10 ...
Scraping page 11 ...
Scraping page 12 ...
Scraping page 13 ...
Scraping page 14 ...
Scraping page 15 ...
Scraping page 16 ...
Scraping page 17 ...
Scraping page 18 ...
Scraping page 19 ...
Scraping page 20 ...
Scraping page 21 ...
Scraping page 22 ...
Scraping page 23 ...
Scraping page 24 ...
Scraping page 25 ...
Scraping page 26 ...
Scraping page 27 ...
Scraping page 28 ...
Scraping page 29 ...
Scraping page 30 ...
Scraping page 31 ...
Scraping page 32 ...
Scraping page 33 ...
Scraping page 34 ...
Scraping page 35 ...
Scraping page 36 ...
Scraping page 37 ...
Scraping page 38 ...
Scraping page 39 ...
Scraping page 40 ...
Scraping page 41 ...
Scraping page 42 ...
Scraping page 43 ...
Scraping page 44 ...
Scraping page 45 ...
Scraping page 46 ...
Scraping page 47 ...
Scraping page 48 ...
S

In [20]:
import sqlite3

DB_NAME = "suumo_listings.db"

def show_all_listings():
    """
    テーブルlistingsに格納されているデータをすべて取得して表示するサンプル関数
    """
    conn = sqlite3.connect(DB_NAME)
    cursor = conn.cursor()

    # listingsテーブルからすべてのカラムを取得 (必要に応じてWHERE句など加えてください)
    select_query = "SELECT id, title, bus_walk, price, management_fee, reikin_shikikin, area, layout, age FROM listings"
    cursor.execute(select_query)
    rows = cursor.fetchall()

    # 取得データの件数表示
    print(f"取得件数: {len(rows)}")
    print("-" * 50)

    # 1行ずつ表示
    for row in rows:
        # rowはタプル形式
        id_, title, bus_walk, price, mgmt_fee, reikin_shikikin, area, layout, age = row
        print(f"[ID] {id_}")
        print(f"  Title: {title}")
        print(f"  バス/徒歩: {bus_walk}")
        print(f"  賃料: {price}")
        print(f"  管理費: {mgmt_fee}")
        print(f"  礼金/敷金: {reikin_shikikin}")
        print(f"  面積: {area}")
        print(f"  間取り: {layout}")
        print(f"  築年数: {age}")
        print("-" * 50)

    conn.close()

if __name__ == "__main__":
    show_all_listings()

取得件数: 17256
--------------------------------------------------
[ID] 1
  Title: 6万円　京急本線/新馬場
  バス/徒歩: ―徒歩5分
  賃料: 6万円
  管理費: 8000円
  礼金/敷金: -(6万円)/6万円
  面積: 17.01m2
  間取り: ワンルーム
  築年数: 築28年
--------------------------------------------------
[ID] 2
  Title: 6万円　京急本線/新馬場
  バス/徒歩: ―徒歩5分
  賃料: 6万円
  管理費: 8000円
  礼金/敷金: -(6万円)/6万円
  面積: 17.01m2
  間取り: ワンルーム
  築年数: 築28年
--------------------------------------------------
[ID] 3
  Title: 6万円　ＪＲ山手線/品川
  バス/徒歩: ―徒歩15分
  賃料: 6万円
  管理費: 8000円
  礼金/敷金: -/6万円
  面積: 17.01m2
  間取り: ワンルーム
  築年数: 築28年
--------------------------------------------------
[ID] 4
  Title: 6万円　ＪＲ京浜東北線/大森
  バス/徒歩: ―徒歩10分
  賃料: 6万円
  管理費: 4000円
  礼金/敷金: 6万円/-
  面積: 21m2
  間取り: 1K
  築年数: 築33年
--------------------------------------------------
[ID] 5
  Title: 6万円　ＪＲ京浜東北線/大井町
  バス/徒歩: ―徒歩14分
  賃料: 6万円
  管理費: -
  礼金/敷金: -/6万円
  面積: 16.1m2
  間取り: 1K
  築年数: 築34年
--------------------------------------------------
[ID] 6
  Title: 6.2万円　京急本線/新馬場
  バス/徒歩: ―徒歩1分
  賃料: 6.2万円
  管理費: 8000円
  